# Setup

In [ ]:
from huggingface_hub import InferenceClient, login

In [ ]:
login()

<div class="alert alert-danger" role="alert" style="display: flex; align-items: center;">
    <div style="text-align: center; padding-right: 10px;">
        <i class="fa fa-exclamation-triangle fa-2x"></i>
    </div>
    <div style="display: flex; align-items: center; margin-top: 4px;"> <!-- Added margin-top to lower the text -->
        <strong>Warning: You will need to point to a model/deployment that is running.</strong>
    </div>
</div>


In [ ]:
MODEL = "CohereForAI/c4ai-command-r-plus"
client = InferenceClient(MODEL)

# Translation
Our goal is to explore translation between English and Arabic and how prompt engineering can impact it. There has been [some work](https://arxiv.org/pdf/2308.01391), but we didn't find as much as we were hoping, especially for open source models.

We have created a dataset across 6 domains and want to compare each method by having human rankers. We also have human translations to ground these rankings.

## Baseline

For our baseline we will translate with a simple system prompt and instruction.

### System Prompt
This is a pretty basic system prompt. We give a role, and an assumed understanding. We also push for goals like "highly motivated and detail-oriented".

> You are a skilled translator with extensive experience in English to Arabic translations. You possess a deep understanding of the linguistic, cultural, and contextual nuances essential for accurate and effective translation between these languages. Highly motivated and detail-oriented, you are committed to delivering translations that maintain the integrity and intent of the original text. Your role is crucial in ensuring clear and precise communication in our multilingual system.

In [ ]:
system_prompt = """You are a skilled translator with extensive experience in English and Arabic translations. You possess a deep understanding of the linguistic, cultural, and contextual nuances essential for accurate and effective translation between these languages. Highly motivated and detail-oriented, you are committed to delivering translations that maintain the integrity and intent of the original text. Your role is crucial in ensuring clear and precise communication in our multilingual system."""

### Instruction
> Translate this from arabic to english: {translation_input}.
>
> Translation:

We will use a simple instruction to get a translation.

In [ ]:
def baseline_chat_completion(system_prompt, translation_input):
    """
    Generates a completion for a chat conversation using a specified system prompt and a user input.
    """
    messages = [
        {"role": "system", "content": system_prompt},
        {
            "role": "user",
            "content": f"Translate this from english to arabic: {translation_input}.\nTranslation: ",
        },
    ]
    return client.chat_completion(messages, max_tokens=10_000)

In [ ]:
translation_input = "Float like a butterfly sting like a bee – his hands can’t hit what his eyes can’t see."
response = baseline_chat_completion(
    system_prompt,
    translation_input,
)

### Token Cost
Here we can see that the cost is quite cheap, only 92 tokens!

In [ ]:
response.usage.prompt_tokens

120

In [ ]:
print(response.choices[0].message.content)

يطير كالفراشة ويلسع كالنحلة - لا يمكن ليديه أن تصيبا ما لا تستطيع عيناه رؤيته.


## Manual Purpose Driven Translation

[Optimizing Machine Translation through Prompt Engineering](https://arxiv.org/pdf/2308.01391) has done some good exploratory work in examining how prompt engineering can impact translation. They were working between Japanese and English and showed that translations influenced by prompts tailored to **specific purposes** and **target audiences** generally adhered more closely to the translation specifications, suggesting that such prompted translations could be more culturally and contextually appropriate than standard machine translations.

### Prompt
One of the approaches in the paper was to include the purpose and target audience specification. This was motivated by the author’s experience as a professional translator, leading to the conclusion that these two parameters are essential even in everyday translation work. You can find the prompt below adapted for Arabic to English:

> Translate the following English [source text] into Arabic. Please fulfill the following conditions when translating.    
> Purpose of the translation: `<Manual description>`  
> Target audience: `<Manual description>`  
> [source text] `{translation_input}`  
> [translated text]

You can see that we need to provide the Purpose and the Target Audience for each translation. This makes sense as we will be able to steer our model appropriately, but the drawback is that we need to do this for each subject. In the real world this likely won't scale and is rather tedious.

Lets go ahead and create these for each of our datasets.

In [ ]:
dataset_to_purpose_target = {
    "ELRC-24ss": {
        "purpose": "Enhancing understanding and knowledge about COVID-19 and health-related topics.",
        "audience": "Individuals seeking reliable and comprehensible information about COVID-19 and related health topics.",
    },
    "GNOME-25ss": {
        "purpose": "Facilitating localization and translation of GNOME software.",
        "audience": "Translators and developers working on GNOME projects."
    },
    "HPLT-25ss": {
        "purpose": "Providing multilingual data for high-performance language technologies.",
        "audience": "Researchers and developers working on multilingual NLP applications."
    },
    "OpenSubtitles-25ss": {
        "purpose": "Creating parallel corpora from movie and TV subtitles.",
        "audience": "Researchers and developers in NLP and machine translation. And Movies and TV Shows translators"
    },
    "TED2020-25ss": {
        "purpose": "Generating multilingual sentence embeddings using TED transcripts.",
        "audience": "Researchers and developers working on multilingual sentence embeddings."
    },
    "UNPC-24ss": {
        "purpose": "Offering a parallel corpus of United Nations documents for linguistic research.",
        "audience": "Researchers and linguists studying multilingual and legal texts."
    }
}


In [ ]:
def purpose_driven_chat_completion(system_prompt, translation_input, dataset):
    """
    Generates a completion for a chat conversation using a specified system prompt and a user input.
    """

    prompt = f"""Translate the following English [source text] into Arabic. Please fulfill the following conditions when translating.
Purpose of the translation: {dataset_to_purpose_target[dataset]['purpose']}
Target audience: {dataset_to_purpose_target[dataset]['audience']}
[source text] `{translation_input}`
[translated text] """

    messages = [
        {"role": "system", "content": system_prompt},
        {
            "role": "user",
            "content": prompt,
        },
    ]
    return client.chat_completion(messages, max_tokens=10_000)

In [ ]:
translation_input = "We have observed that when groups of stakeholders work to define … visions, this leads to debate over whether to emphasize ecosystem health or human well-being … Whether the priority is ecosystems or people greatly influences stakeholders' assessment of desirable ecological and social states."
response = purpose_driven_chat_completion(system_prompt, translation_input, "ELRC-24ss")

In [ ]:
response.usage.prompt_tokens

208

In [ ]:
print(response.choices[0].message.content)

"لقد لاحظنا أنه عندما تعمل مجموعات أصحاب المصلحة على تحديد ... الرؤى، فإن هذا يؤدي إلى نقاش حول ما إذا كان ينبغي التركيز على صحة النظام البيئي أو رفاهية الإنسان ... إن معرفة ما إذا كانت الأولوية للنظم البيئية أو للبشر تؤثر بشكل كبير على تقييم أصحاب المصلحة للحالات البيئية والاجتماعية المرغوبة."


## Automatic Purpose Driven Structured Generation Translation

Manual Purpose Driven Translation is a great step in the right direction, but its challenging to scale. Instead of having the user submit these purposes and target audiences, what if we use a model to do that? The easiest way to get this input in a format that is convenient is going to be by using [structured generation](https://huggingface.co/blog/evaluation-structured-outputs) to get a json. We can easily do this in InferenceClient easily just by using [tools](https://huggingface.co/docs/huggingface_hub/en/package_reference/inference_client#huggingface_hub.InferenceClient.chat_completion.tools)

## Instruction

Its usually helpful if we tell the LLM what we want to create when we prompt it. I have found using the tags like `<source text>` can be really useful to denote what you are specifying.

> I want to translate the following \<source text\> from English into Arabic. But first I want to create a json that includes the following:  
{"intent": "", "subject": "", "assumptions relating to content": "", "purpose": "", "target audience": ""}.  
Can you fill this out and be specific to how this can help you translate in the next step? No need to translate yet!  
\<source text\>  
\</source text\>  

## Tool Definition

In [ ]:
translation_tools = [
    {
        "type": "function",
        "function": {
            "name": "get_translation_audience_purpose",
            "description": "Get the background of a text to assist in translation",
            "parameters": {
                "type": "object",
                "properties": {
                    "subject": {
                        "type": "string",
                        "description": "The topic or central theme that the text revolves around.",
                    },
                    "assumptions relating to the content": {
                        "type": "string",
                        "description": "Write out any assumptions relating to the text.",
                    },
                    "purpose": {
                        "type": "string",
                        "description": "Why the text was written",
                    },
                    "audience": {
                        "type": "string",
                        "description": "The inferred audience that the text is written for.",
                    },
                },
                "required": [
                    "subject",
                    "assumptions relating to the content",
                    "purpose",
                    "audience",
                ],
            },
        },
    }
]

In [ ]:
def tool_call_chat_completion(system_prompt, translation_input, tools):
    """
    Generates a completion for a chat conversation using a specified system prompt and a user input.
    """

    prompt = f"""I want to translate the following <source text> from English into Arabic. But first I want to create a json that includes the following:
{{"subject": "", "assumptions relating to content": "", "purpose": "", "target audience": ""}}.
Can you fill this out and be specific to how this can help you translate in the next step? No need to translate yet!
<source text>
{translation_input}
</source text>
"""
    messages = [
        {"role": "system", "content": system_prompt},
        {
            "role": "user",
            "content": prompt,
        },
    ]
    return client.chat_completion(messages, max_tokens=10_000, tools=tools, tool_choice='get_translation_audience_purpose')

In [ ]:
translation_input = "We have observed that when groups of stakeholders work to define … visions, this leads to debate over whether to emphasize ecosystem health or human well-being … Whether the priority is ecosystems or people greatly influences stakeholders' assessment of desirable ecological and social states."
response = tool_call_chat_completion(system_prompt, translation_input, translation_tools)

In [ ]:
function_call_tokens = response.usage.prompt_tokens
function_call_tokens

454

In [ ]:
from pprint import pprint
description_json = response.choices[0].message.tool_calls[0].function.arguments
pprint(description_json)

{'assumptions relating to the content': 'The text assumes that the readers '
                                        'understand the concept of stakeholder '
                                        'groups and their potential differing '
                                        'priorities regarding environmental '
                                        'and social issues.',
 'audience': 'The target audience for this text is likely individuals or '
             'organizations involved in sustainability, ecology, or social '
             'welfare fields, as well as stakeholders with an interest in '
             'these areas.',
 'purpose': 'The purpose of this text is to highlight the observations made '
            'about the debates that arise when stakeholder groups define their '
            'visions, specifically regarding the priority between ecosystem '
            'health and human well-being, and how this priority influences '
            'their assessment of desired ecological

In [ ]:
def automatic_purpose_driven_chat_completion(system_prompt, translation_input, description_json):
    """
    Generates a completion for a chat conversation using a specified system prompt and a user input.
    """

    prompt = f"""Given the following descriptive json translate <source text> from English to Arabic
{description_json}
<source text>
{translation_input}
</source text>
Translation:
"""
    messages = [
        {"role": "system", "content": system_prompt},
        {
            "role": "user",
            "content": prompt,
        },
    ]
    return client.chat_completion(messages, max_tokens=10_000)

In [ ]:
response = automatic_purpose_driven_chat_completion(system_prompt, translation_input, description_json)

In [ ]:
automatic_purpose_driven_tokens = response.usage.prompt_tokens
automatic_purpose_driven_tokens

311

In [ ]:
print(response.choices[0].message.content)

Here is the translated text from English to Arabic:

{"افتراضات متعلقة بالمحتوى": "يفترض النص أن القراء يفهمون مفهوم مجموعات أصحاب المصلحة وأولوياتهم المختلفة المحتملة فيما يتعلق بالقضايا البيئية والاجتماعية.", "الجمهور": "الجمهور المستهدف لهذا النص هو على الأرجح أفراد أو منظمات تعمل في مجالات الاستدامة أو الإيكولوجيا أو الرعاية الاجتماعية، بالإضافة إلى أصحاب المصلحة المهتمين بهذه المجالات.", "الغرض": "الغرض من هذا النص هو تسليط الضوء على الملاحظات التي أبديت حول النقاشات التي تنشأ عندما تحدد مجموعات أصحاب المصلحة رؤيتها، خاصة فيما يتعلق بالأولوية بين صحة النظام البيئي ورفاهية الإنسان، وكيف تؤثر هذه الأولوية على تقييمها للنتائج الإيكولوجية والاجتماعية المرجوة.", "الموضوع": "النقاشات حول أولويات النظام البيئي مقابل رفاهية الإنسان من قبل مجموعات أصحاب المصلحة": "لقد لاحظنا أنه عندما تعمل مجموعات أصحاب المصلحة على تحديد الرؤى، فإن ذلك يؤدي إلى نقاش حول ما إذا كان ينبغي التركيز على صحة النظام البيئي أو رفاهية الإنسان... إن أولوية النظم البيئية أو البشر تؤثر بشكل كبير على تقييم أصحاب المصلح

# Push to the hub

In [ ]:
from huggingface_hub import HfApi

api = HfApi()
api.upload_file(
    path_or_fileobj="baseline.ipynb",
    path_in_repo="baseline.ipynb",
    repo_id="arabic-translation-prompt-engineering/atpe-notebooks",
    repo_type="model",
)

CommitInfo(commit_url='https://huggingface.co/arabic-translation-prompt-engineering/atpe-notebooks/commit/d112cc49a99a72106b75c3eae9be453264fb488d', commit_message='Upload baseline.ipynb with huggingface_hub', commit_description='', oid='d112cc49a99a72106b75c3eae9be453264fb488d', pr_url=None, pr_revision=None, pr_num=None)